<a href="https://colab.research.google.com/github/flowergum/NN2/blob/task_4/Untitled4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from PIL import Image, ImageFilter
import numpy as np
import requests
from io import BytesIO
import matplotlib.pyplot as plt
from scipy import signal
import tensorflow as tf

In [2]:
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv2D, \
                                    Dense, \
                                    MaxPool2D,\
                                    Dropout, \
                                    Flatten, \
                                    BatchNormalization
from tensorflow.keras.datasets import mnist

In [3]:
%matplotlib inline
import seaborn as sns

In [4]:
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
  try:
    # Currently, memory growth needs to be the same across GPUs
    for gpu in gpus:
      tf.config.experimental.set_memory_growth(gpu, True)
    logical_gpus = tf.config.experimental.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
  except RuntimeError as e:
    # Memory growth must be set before GPUs have been initialized
    print(e)

In [5]:
(x_train, y_train),(x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0
# Reshape the images.
x_train = np.expand_dims(x_train, axis=3)
x_test = np.expand_dims(x_test, axis=3)
input_shape = x_train[0].shape

11493376/11490434 [==============================] - 0s 0us/step


In [8]:
model = Sequential([
  Conv2D(32,kernel_size=(3,3), input_shape=input_shape, activation ='relu', padding='same'),
	Conv2D(32,kernel_size=(3,3), activation ='relu', padding='same'),
	MaxPool2D(pool_size=(2, 2)),
	

	Conv2D(64,kernel_size=(3,3), activation ='relu', padding = 'same'),
	Conv2D(64,kernel_size=(3,3), activation ='relu', padding='same'),
  MaxPool2D(pool_size=(2, 2)),
    
	Flatten(),
  Dense(128, activation=tf.nn.relu),
  Dropout(0.25),
  Dense(10, activation=tf.nn.softmax)])

In [9]:
model.compile(optimizer="adam",
              loss=tf.keras.losses.sparse_categorical_crossentropy,
              metrics=['accuracy'])

In [10]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 28, 28, 32)        320       
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 28, 28, 32)        9248      
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 14, 14, 32)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 14, 14, 64)        18496     
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 14, 14, 64)        36928     
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 7, 7, 64)          0         
_________________________________________________________________
flatten (Flatten)            (None, 3136)              0

In [ ]:
history = model.fit(x_train,
                    y_train,
                    epochs=1,
                    validation_data=(x_test, y_test))

In [ ]:
loss, acc = model.evaluate(x_train, y_train)
print("Loss = {}, accuracy = {}".format(loss, acc))

In [ ]:
loss, acc = model.evaluate(x_test, y_test)
print("Loss = {}, accuracy = {}".format(loss, acc))

✅ Задание 2:
Вывести слои активации модели нейронной сети, то есть изображения, прошедшие через слои нейронной сети.

Найти в документации Tensorflow как достать слои активации
Найти в документации или в примерах Matplotlib как вывести несколько изображений близко к друг-другу
Поскольку изображения будут не в диапазоне (0, 255), то найти как вывести тепловую карту
Вывести несколько слоёв активации для свёрточной модели

In [125]:
def draw(layer):
    a, dim_1,dim_2,dim_3 = layer.shape
    fig, axarr = plt.subplots(nrows = dim_3 // 16, ncols = 16, gridspec_kw={'hspace':0, 'wspace':0})
    reshape_layer_activation = [[[layer[0,i,j,k] for i in range(dim_1)] for j in range(dim_2)] for k in range(dim_3)]

    fig.set_figwidth(448)
    fig.set_figheight(28 * dim_3 // 16 + 2)
    for i in range(dim_3):
        axarr[i // 16][i % 16].imshow(reshape_layer_activation[i])
        axarr[i // 16][i % 16].axis('off')
    fig.suptitle('name')
    plt.show()

In [126]:
layer_outputs = [layer.output for layer in model.layers[:-1]]
activation_model = tf.keras.Model(inputs = model.input, outputs = layer_outputs)

test_im = x_train[2979] # Random image
activations = activation_model.predict(test_im.reshape(1,28,28,1))

layer_activation = activations[0]
x = len(activations)

# DRAW PLOTS
for i in range(x-3):
    draw(activations[i])

In [114]:
for i in range(len(activations) - 3):
    print(activations[i].shape)

(1, 28, 28, 32)
(1, 28, 28, 32)
(1, 14, 14, 32)
(1, 14, 14, 64)
(1, 14, 14, 64)
(1, 7, 7, 64)
